In [1]:
import numpy as np
import pandas as pd
from pandas.tseries.offsets import Hour, Minute
from pandas.tseries.offsets import Day, MonthEnd
from pandas.tseries.offsets import Hour
from statsmodels.tsa.arima.model import ARIMA
from pmdarima.arima import auto_arima
from sklearn.model_selection import TimeSeriesSplit
from sklearn.metrics import mean_squared_error as mse
from time import time



In [2]:
def TrainTest(df):
    
    num_rows = df.shape[0]
    
    num_training = (num_rows * 8)//10
   
    #train = df.iloc[0:num_training]
    #test = df.iloc[num_training:num_rows]
    
    
    return num_training 
        
            
        
            

In [3]:


#df = pd.read_csv('Wind_deseason.csv')
df = pd.read_csv('Wind_deseason_15.csv', parse_dates=[0], index_col=0)


In [4]:
def runAutoArima(df):
    autoAR = auto_arima(df['309_WIND_1'], trace = True, random_state = 102)
    autoAR.summary()

In [5]:
def TestModel(test, mod, train):
    
    MSEs = []
    
    length = len(train)
    
    for i in range(len(test)):
       
        start = length + i
        end = length + i +1
        
        pred = mod.predict()
        print(pred)
        
        
        print(pred[0])
        print(test['309_WIND_1'][i])
        
        MSEs.append((test['309_WIND_1'][i] - pred[0])**2)
        
        
        
    return MSEs

In [6]:

def model1Train(train, params):

            
    
    start = time()
    mod = ARIMA(train['309_WIND_1'],order = params)
    result = mod.fit()
    print('auto time')
    print(time()-start)
    

        
    return result

    

In [7]:
def model2Train(train):
    start = time()
    mod = ARIMA( train['309_WIND_1'], order = (2,1,20))
    result = mod.fit()
    print('acf time')
    print(time()-start)
    
    return result
    

In [8]:
def model3(tss,df):

    mse3 = []

    for train_indx, val_indx in tss.split(df):
        train = df.iloc[train_indx]
        test = df.iloc[val_indx]
    
        pred = train['309_WIND_1'][-1]
    
    
        error = 0.5*(test['309_WIND_1'][0] - pred)**2
        mse3.append(error)
        
    print(mse3)
    return mse3


In [9]:
def runModels(df, params):
    
    bound = TrainTest(df)
    
    train = df[0:bound]
    test = df[bound:]

  
    model1 = model1Train(train, params)
    model2 = model2Train(train)
    
    mse1 = TestModel(test, model1, train)
    mse2 = TestModel(test, model2, train)
    
    
    return mse1, mse2

    

In [10]:

df1 = df[df.index.month.isin([1,2,3])]
df2 = df[df.index.month.isin([4,5,6])]
df3 = df[df.index.month.isin([7,8,9])]
df4 = df[df.index.month.isin([10,11,12])]

In [11]:
bound = TrainTest(df1)
train1 = df1[0:bound]

runAutoArima(train1) #--> result (1,1,3)

Performing stepwise search to minimize aic
 ARIMA(2,1,2)(0,0,0)[0] intercept   : AIC=46128.102, Time=4.91 sec
 ARIMA(0,1,0)(0,0,0)[0] intercept   : AIC=47760.425, Time=0.16 sec
 ARIMA(1,1,0)(0,0,0)[0] intercept   : AIC=46130.304, Time=0.31 sec
 ARIMA(0,1,1)(0,0,0)[0] intercept   : AIC=46368.571, Time=0.71 sec
 ARIMA(0,1,0)(0,0,0)[0]             : AIC=47758.449, Time=0.13 sec
 ARIMA(1,1,2)(0,0,0)[0] intercept   : AIC=46130.295, Time=1.42 sec
 ARIMA(2,1,1)(0,0,0)[0] intercept   : AIC=46132.931, Time=1.44 sec
 ARIMA(3,1,2)(0,0,0)[0] intercept   : AIC=46129.043, Time=8.84 sec
 ARIMA(2,1,3)(0,0,0)[0] intercept   : AIC=46109.193, Time=4.62 sec
 ARIMA(1,1,3)(0,0,0)[0] intercept   : AIC=46107.218, Time=2.91 sec
 ARIMA(0,1,3)(0,0,0)[0] intercept   : AIC=46114.123, Time=1.48 sec
 ARIMA(1,1,4)(0,0,0)[0] intercept   : AIC=inf, Time=10.80 sec
 ARIMA(0,1,2)(0,0,0)[0] intercept   : AIC=46173.512, Time=1.02 sec
 ARIMA(0,1,4)(0,0,0)[0] intercept   : AIC=46110.601, Time=1.79 sec
 ARIMA(2,1,4)(0,0,0)[0] 

In [31]:
#bound = TrainTest(df2)
#train2 = df2[0:bound]

#runAutoArima(train2) #--> result (2,1,0)

In [32]:
#bound = TrainTest(df3)
#train3 = df3[0:bound]

#runAutoArima(train3) #--> result (3,0,1)

In [33]:
#bound = TrainTest(df4)
#train4 = df[0:bound]
#
#runAutoArima(train4) # --> result (3,1,1)

In [12]:
mse1, mse2 = runModels(df1, (1,1,3))

C:\Users\bvits\anaconda3\envs\modern_ts\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: No frequency information was provided, so inferred frequency 15T will be used.
  self._init_dates(dates, freq)
C:\Users\bvits\anaconda3\envs\modern_ts\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: No frequency information was provided, so inferred frequency 15T will be used.
  self._init_dates(dates, freq)
C:\Users\bvits\anaconda3\envs\modern_ts\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: No frequency information was provided, so inferred frequency 15T will be used.
  self._init_dates(dates, freq)


auto time
1.472423791885376


C:\Users\bvits\anaconda3\envs\modern_ts\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: No frequency information was provided, so inferred frequency 15T will be used.
  self._init_dates(dates, freq)
C:\Users\bvits\anaconda3\envs\modern_ts\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: No frequency information was provided, so inferred frequency 15T will be used.
  self._init_dates(dates, freq)
C:\Users\bvits\anaconda3\envs\modern_ts\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: No frequency information was provided, so inferred frequency 15T will be used.
  self._init_dates(dates, freq)


acf time
45.667879581451416
2020-01-01 00:15:00     0.000000
2020-01-01 00:30:00    59.032479
2020-01-01 00:45:00    58.844602
2020-01-01 01:00:00    60.866861
2020-01-01 01:15:00    59.459230
                         ...    
2020-03-13 18:00:00   -29.373767
2020-03-13 18:15:00   -32.194817
2020-03-13 18:30:00   -30.896119
2020-03-13 18:45:00   -30.296289
2020-03-13 19:00:00   -34.869252
Freq: 15T, Name: predicted_mean, Length: 6988, dtype: float64
0.0
-35.25189187235375
2020-01-01 00:15:00     0.000000
2020-01-01 00:30:00    59.032479
2020-01-01 00:45:00    58.844602
2020-01-01 01:00:00    60.866861
2020-01-01 01:15:00    59.459230
                         ...    
2020-03-13 18:00:00   -29.373767
2020-03-13 18:15:00   -32.194817
2020-03-13 18:30:00   -30.896119
2020-03-13 18:45:00   -30.296289
2020-03-13 19:00:00   -34.869252
Freq: 15T, Name: predicted_mean, Length: 6988, dtype: float64
0.0
-35.44727241993393
2020-01-01 00:15:00     0.000000
2020-01-01 00:30:00    59.032479
2020-01-01

2020-01-01 00:15:00     0.000000
2020-01-01 00:30:00    59.032479
2020-01-01 00:45:00    58.844602
2020-01-01 01:00:00    60.866861
2020-01-01 01:15:00    59.459230
                         ...    
2020-03-13 18:00:00   -29.373767
2020-03-13 18:15:00   -32.194817
2020-03-13 18:30:00   -30.896119
2020-03-13 18:45:00   -30.296289
2020-03-13 19:00:00   -34.869252
Freq: 15T, Name: predicted_mean, Length: 6988, dtype: float64
0.0
-36.747158780185416
2020-01-01 00:15:00     0.000000
2020-01-01 00:30:00    59.032479
2020-01-01 00:45:00    58.844602
2020-01-01 01:00:00    60.866861
2020-01-01 01:15:00    59.459230
                         ...    
2020-03-13 18:00:00   -29.373767
2020-03-13 18:15:00   -32.194817
2020-03-13 18:30:00   -30.896119
2020-03-13 18:45:00   -30.296289
2020-03-13 19:00:00   -34.869252
Freq: 15T, Name: predicted_mean, Length: 6988, dtype: float64
0.0
-33.44255404486135
2020-01-01 00:15:00     0.000000
2020-01-01 00:30:00    59.032479
2020-01-01 00:45:00    58.844602
2020

...

2020-01-01 00:15:00     0.000000
2020-01-01 00:30:00    59.032492
2020-01-01 00:45:00    58.844224
2020-01-01 01:00:00    60.866320
2020-01-01 01:15:00    59.459656
                         ...    
2020-03-13 18:00:00   -28.722210
2020-03-13 18:15:00   -31.421466
2020-03-13 18:30:00   -29.877469
2020-03-13 18:45:00   -29.764769
2020-03-13 19:00:00   -34.372804
Freq: 15T, Name: predicted_mean, Length: 6988, dtype: float64
0.0
67.3714489513237
2020-01-01 00:15:00     0.000000
2020-01-01 00:30:00    59.032492
2020-01-01 00:45:00    58.844224
2020-01-01 01:00:00    60.866320
2020-01-01 01:15:00    59.459656
                         ...    
2020-03-13 18:00:00   -28.722210
2020-03-13 18:15:00   -31.421466
2020-03-13 18:30:00   -29.877469
2020-03-13 18:45:00   -29.764769
2020-03-13 19:00:00   -34.372804
Freq: 15T, Name: predicted_mean, Length: 6988, dtype: float64
0.0
66.9760179631363
2020-01-01 00:15:00     0.000000
2020-01-01 00:30:00    59.032492
2020-01-01 00:45:00    58.844224
2020-01-0

2020-01-01 00:15:00     0.000000
2020-01-01 00:30:00    59.032492
2020-01-01 00:45:00    58.844224
2020-01-01 01:00:00    60.866320
2020-01-01 01:15:00    59.459656
                         ...    
2020-03-13 18:00:00   -28.722210
2020-03-13 18:15:00   -31.421466
2020-03-13 18:30:00   -29.877469
2020-03-13 18:45:00   -29.764769
2020-03-13 19:00:00   -34.372804
Freq: 15T, Name: predicted_mean, Length: 6988, dtype: float64
0.0
-31.31207378205783
2020-01-01 00:15:00     0.000000
2020-01-01 00:30:00    59.032492
2020-01-01 00:45:00    58.844224
2020-01-01 01:00:00    60.866320
2020-01-01 01:15:00    59.459656
                         ...    
2020-03-13 18:00:00   -28.722210
2020-03-13 18:15:00   -31.421466
2020-03-13 18:30:00   -29.877469
2020-03-13 18:45:00   -29.764769
2020-03-13 19:00:00   -34.372804
Freq: 15T, Name: predicted_mean, Length: 6988, dtype: float64
0.0
-32.40750477024523
2020-01-01 00:15:00     0.000000
2020-01-01 00:30:00    59.032492
2020-01-01 00:45:00    58.844224
2020-

2020-01-01 00:15:00     0.000000
2020-01-01 00:30:00    59.032492
2020-01-01 00:45:00    58.844224
2020-01-01 01:00:00    60.866320
2020-01-01 01:15:00    59.459656
                         ...    
2020-03-13 18:00:00   -28.722210
2020-03-13 18:15:00   -31.421466
2020-03-13 18:30:00   -29.877469
2020-03-13 18:45:00   -29.764769
2020-03-13 19:00:00   -34.372804
Freq: 15T, Name: predicted_mean, Length: 6988, dtype: float64
0.0
15.219367847215768
2020-01-01 00:15:00     0.000000
2020-01-01 00:30:00    59.032492
2020-01-01 00:45:00    58.844224
2020-01-01 01:00:00    60.866320
2020-01-01 01:15:00    59.459656
                         ...    
2020-03-13 18:00:00   -28.722210
2020-03-13 18:15:00   -31.421466
2020-03-13 18:30:00   -29.877469
2020-03-13 18:45:00   -29.764769
2020-03-13 19:00:00   -34.372804
Freq: 15T, Name: predicted_mean, Length: 6988, dtype: float64
0.0
4.990588498165717
2020-01-01 00:15:00     0.000000
2020-01-01 00:30:00    59.032492
2020-01-01 00:45:00    58.844224
2020-0

2020-01-01 00:15:00     0.000000
2020-01-01 00:30:00    59.032492
2020-01-01 00:45:00    58.844224
2020-01-01 01:00:00    60.866320
2020-01-01 01:15:00    59.459656
                         ...    
2020-03-13 18:00:00   -28.722210
2020-03-13 18:15:00   -31.421466
2020-03-13 18:30:00   -29.877469
2020-03-13 18:45:00   -29.764769
2020-03-13 19:00:00   -34.372804
Freq: 15T, Name: predicted_mean, Length: 6988, dtype: float64
0.0
-39.06351190823623
2020-01-01 00:15:00     0.000000
2020-01-01 00:30:00    59.032492
2020-01-01 00:45:00    58.844224
2020-01-01 01:00:00    60.866320
2020-01-01 01:15:00    59.459656
                         ...    
2020-03-13 18:00:00   -28.722210
2020-03-13 18:15:00   -31.421466
2020-03-13 18:30:00   -29.877469
2020-03-13 18:45:00   -29.764769
2020-03-13 19:00:00   -34.372804
Freq: 15T, Name: predicted_mean, Length: 6988, dtype: float64
0.0
-37.72562459061961
2020-01-01 00:15:00     0.000000
2020-01-01 00:30:00    59.032492
2020-01-01 00:45:00    58.844224
2020-

2020-01-01 00:15:00     0.000000
2020-01-01 00:30:00    59.032492
2020-01-01 00:45:00    58.844224
2020-01-01 01:00:00    60.866320
2020-01-01 01:15:00    59.459656
                         ...    
2020-03-13 18:00:00   -28.722210
2020-03-13 18:15:00   -31.421466
2020-03-13 18:30:00   -29.877469
2020-03-13 18:45:00   -29.764769
2020-03-13 19:00:00   -34.372804
Freq: 15T, Name: predicted_mean, Length: 6988, dtype: float64
0.0
-28.76457276793738
2020-01-01 00:15:00     0.000000
2020-01-01 00:30:00    59.032492
2020-01-01 00:45:00    58.844224
2020-01-01 01:00:00    60.866320
2020-01-01 01:15:00    59.459656
                         ...    
2020-03-13 18:00:00   -28.722210
2020-03-13 18:15:00   -31.421466
2020-03-13 18:30:00   -29.877469
2020-03-13 18:45:00   -29.764769
2020-03-13 19:00:00   -34.372804
Freq: 15T, Name: predicted_mean, Length: 6988, dtype: float64
0.0
-28.99335211698743
2020-01-01 00:15:00     0.000000
2020-01-01 00:30:00    59.032492
2020-01-01 00:45:00    58.844224
2020-

In [35]:
mse3, mse4 = runModels(df2, (2,1,0))

C:\Users\bvits\anaconda3\envs\modern_ts\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: No frequency information was provided, so inferred frequency 15T will be used.
  self._init_dates(dates, freq)
C:\Users\bvits\anaconda3\envs\modern_ts\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: No frequency information was provided, so inferred frequency 15T will be used.
  self._init_dates(dates, freq)
C:\Users\bvits\anaconda3\envs\modern_ts\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: No frequency information was provided, so inferred frequency 15T will be used.
  self._init_dates(dates, freq)
C:\Users\bvits\anaconda3\envs\modern_ts\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: No frequency information was provided, so inferred frequency 15T will be used.
  self._init_dates(dates, freq)
C:\Users\bvits\anaconda3\envs\modern_ts\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: N

2020-04-01 00:00:00     0.000000
2020-04-01 00:15:00   -42.917467
2020-04-01 00:30:00   -42.383694
2020-04-01 00:45:00   -42.564690
2020-04-01 01:00:00   -43.120335
                         ...    
2020-06-12 17:45:00   -20.937257
2020-06-12 18:00:00   -20.208997
2020-06-12 18:15:00   -17.373002
2020-06-12 18:30:00   -18.727643
2020-06-12 18:45:00   -19.167992
Freq: 15T, Name: predicted_mean, Length: 6988, dtype: float64
0.0
-20.89419052438829
2020-04-01 00:00:00     0.000000
2020-04-01 00:15:00   -42.917467
2020-04-01 00:30:00   -42.383694
2020-04-01 00:45:00   -42.564690
2020-04-01 01:00:00   -43.120335
                         ...    
2020-06-12 17:45:00   -20.937257
2020-06-12 18:00:00   -20.208997
2020-06-12 18:15:00   -17.373002
2020-06-12 18:30:00   -18.727643
2020-06-12 18:45:00   -19.167992
Freq: 15T, Name: predicted_mean, Length: 6988, dtype: float64
0.0
-20.959737118541536
2020-04-01 00:00:00     0.000000
2020-04-01 00:15:00   -42.917467
2020-04-01 00:30:00   -42.383694
2020

2020-04-01 00:00:00     0.000000
2020-04-01 00:15:00   -42.917467
2020-04-01 00:30:00   -42.383694
2020-04-01 00:45:00   -42.564690
2020-04-01 01:00:00   -43.120335
                         ...    
2020-06-12 17:45:00   -20.937257
2020-06-12 18:00:00   -20.208997
2020-06-12 18:15:00   -17.373002
2020-06-12 18:30:00   -18.727643
2020-06-12 18:45:00   -19.167992
Freq: 15T, Name: predicted_mean, Length: 6988, dtype: float64
0.0
-22.576974842803796
2020-04-01 00:00:00     0.000000
2020-04-01 00:15:00   -42.917467
2020-04-01 00:30:00   -42.383694
2020-04-01 00:45:00   -42.564690
2020-04-01 01:00:00   -43.120335
                         ...    
2020-06-12 17:45:00   -20.937257
2020-06-12 18:00:00   -20.208997
2020-06-12 18:15:00   -17.373002
2020-06-12 18:30:00   -18.727643
2020-06-12 18:45:00   -19.167992
Freq: 15T, Name: predicted_mean, Length: 6988, dtype: float64
0.0
-22.609318820554776
2020-04-01 00:00:00     0.000000
2020-04-01 00:15:00   -42.917467
2020-04-01 00:30:00   -42.383694
202

2020-04-01 00:00:00     0.000000
2020-04-01 00:15:00   -42.917467
2020-04-01 00:30:00   -42.383694
2020-04-01 00:45:00   -42.564690
2020-04-01 01:00:00   -43.120335
                         ...    
2020-06-12 17:45:00   -20.937257
2020-06-12 18:00:00   -20.208997
2020-06-12 18:15:00   -17.373002
2020-06-12 18:30:00   -18.727643
2020-06-12 18:45:00   -19.167992
Freq: 15T, Name: predicted_mean, Length: 6988, dtype: float64
0.0
21.65968949563454
2020-04-01 00:00:00     0.000000
2020-04-01 00:15:00   -42.917467
2020-04-01 00:30:00   -42.383694
2020-04-01 00:45:00   -42.564690
2020-04-01 01:00:00   -43.120335
                         ...    
2020-06-12 17:45:00   -20.937257
2020-06-12 18:00:00   -20.208997
2020-06-12 18:15:00   -17.373002
2020-06-12 18:30:00   -18.727643
2020-06-12 18:45:00   -19.167992
Freq: 15T, Name: predicted_mean, Length: 6988, dtype: float64
0.0
5.060678851216892
2020-04-01 00:00:00     0.000000
2020-04-01 00:15:00   -42.917467
2020-04-01 00:30:00   -42.383694
2020-04

2020-04-01 00:00:00     0.000000
2020-04-01 00:15:00   -42.917467
2020-04-01 00:30:00   -42.383694
2020-04-01 00:45:00   -42.564690
2020-04-01 01:00:00   -43.120335
                         ...    
2020-06-12 17:45:00   -20.937257
2020-06-12 18:00:00   -20.208997
2020-06-12 18:15:00   -17.373002
2020-06-12 18:30:00   -18.727643
2020-06-12 18:45:00   -19.167992
Freq: 15T, Name: predicted_mean, Length: 6988, dtype: float64
0.0
-27.48886767149514
2020-04-01 00:00:00     0.000000
2020-04-01 00:15:00   -42.917467
2020-04-01 00:30:00   -42.383694
2020-04-01 00:45:00   -42.564690
2020-04-01 01:00:00   -43.120335
                         ...    
2020-06-12 17:45:00   -20.937257
2020-06-12 18:00:00   -20.208997
2020-06-12 18:15:00   -17.373002
2020-06-12 18:30:00   -18.727643
2020-06-12 18:45:00   -19.167992
Freq: 15T, Name: predicted_mean, Length: 6988, dtype: float64
0.0
-21.421211649246125
2020-04-01 00:00:00     0.000000
2020-04-01 00:15:00   -42.917467
2020-04-01 00:30:00   -42.383694
2020

...

2020-04-01 00:00:00     0.000000
2020-04-01 00:15:00   -42.917469
2020-04-01 00:30:00   -42.383793
2020-04-01 00:45:00   -42.564692
2020-04-01 01:00:00   -43.123922
                         ...    
2020-06-12 17:45:00   -19.981058
2020-06-12 18:00:00   -19.346907
2020-06-12 18:15:00   -16.457007
2020-06-12 18:30:00   -17.809845
2020-06-12 18:45:00   -18.283423
Freq: 15T, Name: predicted_mean, Length: 6988, dtype: float64
0.0
-20.47200450803908
2020-04-01 00:00:00     0.000000
2020-04-01 00:15:00   -42.917469
2020-04-01 00:30:00   -42.383793
2020-04-01 00:45:00   -42.564692
2020-04-01 01:00:00   -43.123922
                         ...    
2020-06-12 17:45:00   -19.981058
2020-06-12 18:00:00   -19.346907
2020-06-12 18:15:00   -16.457007
2020-06-12 18:30:00   -17.809845
2020-06-12 18:45:00   -18.283423
Freq: 15T, Name: predicted_mean, Length: 6988, dtype: float64
0.0
-19.671312503136093
2020-04-01 00:00:00     0.000000
2020-04-01 00:15:00   -42.917469
2020-04-01 00:30:00   -42.383793
2020

2020-04-01 00:00:00     0.000000
2020-04-01 00:15:00   -42.917469
2020-04-01 00:30:00   -42.383793
2020-04-01 00:45:00   -42.564692
2020-04-01 01:00:00   -43.123922
                         ...    
2020-06-12 17:45:00   -19.981058
2020-06-12 18:00:00   -19.346907
2020-06-12 18:15:00   -16.457007
2020-06-12 18:30:00   -17.809845
2020-06-12 18:45:00   -18.283423
Freq: 15T, Name: predicted_mean, Length: 6988, dtype: float64
0.0
-25.4736469790905
2020-04-01 00:00:00     0.000000
2020-04-01 00:15:00   -42.917469
2020-04-01 00:30:00   -42.383793
2020-04-01 00:45:00   -42.564692
2020-04-01 01:00:00   -43.123922
                         ...    
2020-06-12 17:45:00   -19.981058
2020-06-12 18:00:00   -19.346907
2020-06-12 18:15:00   -16.457007
2020-06-12 18:30:00   -17.809845
2020-06-12 18:45:00   -18.283423
Freq: 15T, Name: predicted_mean, Length: 6988, dtype: float64
0.0
-26.17295497418751
2020-04-01 00:00:00     0.000000
2020-04-01 00:15:00   -42.917469
2020-04-01 00:30:00   -42.383793
2020-0

2020-04-01 00:00:00     0.000000
2020-04-01 00:15:00   -42.917469
2020-04-01 00:30:00   -42.383793
2020-04-01 00:45:00   -42.564692
2020-04-01 01:00:00   -43.123922
                         ...    
2020-06-12 17:45:00   -19.981058
2020-06-12 18:00:00   -19.346907
2020-06-12 18:15:00   -16.457007
2020-06-12 18:30:00   -17.809845
2020-06-12 18:45:00   -18.283423
Freq: 15T, Name: predicted_mean, Length: 6988, dtype: float64
0.0
-10.415692552031135
2020-04-01 00:00:00     0.000000
2020-04-01 00:15:00   -42.917469
2020-04-01 00:30:00   -42.383793
2020-04-01 00:45:00   -42.564692
2020-04-01 01:00:00   -43.123922
                         ...    
2020-06-12 17:45:00   -19.981058
2020-06-12 18:00:00   -19.346907
2020-06-12 18:15:00   -16.457007
2020-06-12 18:30:00   -17.809845
2020-06-12 18:45:00   -18.283423
Freq: 15T, Name: predicted_mean, Length: 6988, dtype: float64
0.0
-10.848333880461478
2020-04-01 00:00:00     0.000000
2020-04-01 00:15:00   -42.917469
2020-04-01 00:30:00   -42.383793
202

2020-04-01 00:00:00     0.000000
2020-04-01 00:15:00   -42.917469
2020-04-01 00:30:00   -42.383793
2020-04-01 00:45:00   -42.564692
2020-04-01 01:00:00   -43.123922
                         ...    
2020-06-12 17:45:00   -19.981058
2020-06-12 18:00:00   -19.346907
2020-06-12 18:15:00   -16.457007
2020-06-12 18:30:00   -17.809845
2020-06-12 18:45:00   -18.283423
Freq: 15T, Name: predicted_mean, Length: 6988, dtype: float64
0.0
-16.409144847848214
2020-04-01 00:00:00     0.000000
2020-04-01 00:15:00   -42.917469
2020-04-01 00:30:00   -42.383793
2020-04-01 00:45:00   -42.564692
2020-04-01 01:00:00   -43.123922
                         ...    
2020-06-12 17:45:00   -19.981058
2020-06-12 18:00:00   -19.346907
2020-06-12 18:15:00   -16.457007
2020-06-12 18:30:00   -17.809845
2020-06-12 18:45:00   -18.283423
Freq: 15T, Name: predicted_mean, Length: 6988, dtype: float64
0.0
-16.60851819892783
2020-04-01 00:00:00     0.000000
2020-04-01 00:15:00   -42.917469
2020-04-01 00:30:00   -42.383793
2020

2020-04-01 00:00:00     0.000000
2020-04-01 00:15:00   -42.917469
2020-04-01 00:30:00   -42.383793
2020-04-01 00:45:00   -42.564692
2020-04-01 01:00:00   -43.123922
                         ...    
2020-06-12 17:45:00   -19.981058
2020-06-12 18:00:00   -19.346907
2020-06-12 18:15:00   -16.457007
2020-06-12 18:30:00   -17.809845
2020-06-12 18:45:00   -18.283423
Freq: 15T, Name: predicted_mean, Length: 6988, dtype: float64
0.0
-17.3116951066606
2020-04-01 00:00:00     0.000000
2020-04-01 00:15:00   -42.917469
2020-04-01 00:30:00   -42.383793
2020-04-01 00:45:00   -42.564692
2020-04-01 01:00:00   -43.123922
                         ...    
2020-06-12 17:45:00   -19.981058
2020-06-12 18:00:00   -19.346907
2020-06-12 18:15:00   -16.457007
2020-06-12 18:30:00   -17.809845
2020-06-12 18:45:00   -18.283423
Freq: 15T, Name: predicted_mean, Length: 6988, dtype: float64
0.0
-17.577735124406885
2020-04-01 00:00:00     0.000000
2020-04-01 00:15:00   -42.917469
2020-04-01 00:30:00   -42.383793
2020-

In [36]:
mse5, mse6 = runModels(df3, (3,0,1))

C:\Users\bvits\anaconda3\envs\modern_ts\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: No frequency information was provided, so inferred frequency 15T will be used.
  self._init_dates(dates, freq)
C:\Users\bvits\anaconda3\envs\modern_ts\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: No frequency information was provided, so inferred frequency 15T will be used.
  self._init_dates(dates, freq)
C:\Users\bvits\anaconda3\envs\modern_ts\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: No frequency information was provided, so inferred frequency 15T will be used.
  self._init_dates(dates, freq)
C:\Users\bvits\anaconda3\envs\modern_ts\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: No frequency information was provided, so inferred frequency 15T will be used.
  self._init_dates(dates, freq)
C:\Users\bvits\anaconda3\envs\modern_ts\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: N

2020-07-01 00:00:00     3.934172
2020-07-01 00:15:00    20.451124
2020-07-01 00:30:00    45.018614
2020-07-01 00:45:00    42.100933
2020-07-01 01:00:00    54.247559
                         ...    
2020-09-12 13:00:00    53.593651
2020-09-12 13:15:00    46.486775
2020-09-12 13:30:00    25.772109
2020-09-12 13:45:00    35.940168
2020-09-12 14:00:00    21.367652
Freq: 15T, Name: predicted_mean, Length: 7065, dtype: float64
3.9341719584649053
20.5708444203473
2020-07-01 00:00:00     3.934172
2020-07-01 00:15:00    20.451124
2020-07-01 00:30:00    45.018614
2020-07-01 00:45:00    42.100933
2020-07-01 01:00:00    54.247559
                         ...    
2020-09-12 13:00:00    53.593651
2020-09-12 13:15:00    46.486775
2020-09-12 13:30:00    25.772109
2020-09-12 13:45:00    35.940168
2020-09-12 14:00:00    21.367652
Freq: 15T, Name: predicted_mean, Length: 7065, dtype: float64
3.9341719584649053
18.769072205693945
2020-07-01 00:00:00     3.934172
2020-07-01 00:15:00    20.451124
2020-07-01

2020-07-01 00:00:00     3.934172
2020-07-01 00:15:00    20.451124
2020-07-01 00:30:00    45.018614
2020-07-01 00:45:00    42.100933
2020-07-01 01:00:00    54.247559
                         ...    
2020-09-12 13:00:00    53.593651
2020-09-12 13:15:00    46.486775
2020-09-12 13:30:00    25.772109
2020-09-12 13:45:00    35.940168
2020-09-12 14:00:00    21.367652
Freq: 15T, Name: predicted_mean, Length: 7065, dtype: float64
3.9341719584649053
-14.576925364575796
2020-07-01 00:00:00     3.934172
2020-07-01 00:15:00    20.451124
2020-07-01 00:30:00    45.018614
2020-07-01 00:45:00    42.100933
2020-07-01 01:00:00    54.247559
                         ...    
2020-09-12 13:00:00    53.593651
2020-09-12 13:15:00    46.486775
2020-09-12 13:30:00    25.772109
2020-09-12 13:45:00    35.940168
2020-09-12 14:00:00    21.367652
Freq: 15T, Name: predicted_mean, Length: 7065, dtype: float64
3.9341719584649053
-14.345576803114913
2020-07-01 00:00:00     3.934172
2020-07-01 00:15:00    20.451124
2020-0

2020-07-01 00:00:00     3.934172
2020-07-01 00:15:00    20.451124
2020-07-01 00:30:00    45.018614
2020-07-01 00:45:00    42.100933
2020-07-01 01:00:00    54.247559
                         ...    
2020-09-12 13:00:00    53.593651
2020-09-12 13:15:00    46.486775
2020-09-12 13:30:00    25.772109
2020-09-12 13:45:00    35.940168
2020-09-12 14:00:00    21.367652
Freq: 15T, Name: predicted_mean, Length: 7065, dtype: float64
3.9341719584649053
-22.89520218399037
2020-07-01 00:00:00     3.934172
2020-07-01 00:15:00    20.451124
2020-07-01 00:30:00    45.018614
2020-07-01 00:45:00    42.100933
2020-07-01 01:00:00    54.247559
                         ...    
2020-09-12 13:00:00    53.593651
2020-09-12 13:15:00    46.486775
2020-09-12 13:30:00    25.772109
2020-09-12 13:45:00    35.940168
2020-09-12 14:00:00    21.367652
Freq: 15T, Name: predicted_mean, Length: 7065, dtype: float64
3.9341719584649053
-23.03052028919616
2020-07-01 00:00:00     3.934172
2020-07-01 00:15:00    20.451124
2020-07-

2020-07-01 00:00:00     3.934172
2020-07-01 00:15:00    20.451124
2020-07-01 00:30:00    45.018614
2020-07-01 00:45:00    42.100933
2020-07-01 01:00:00    54.247559
                         ...    
2020-09-12 13:00:00    53.593651
2020-09-12 13:15:00    46.486775
2020-09-12 13:30:00    25.772109
2020-09-12 13:45:00    35.940168
2020-09-12 14:00:00    21.367652
Freq: 15T, Name: predicted_mean, Length: 7065, dtype: float64
3.9341719584649053
-31.777220928893662
2020-07-01 00:00:00     3.934172
2020-07-01 00:15:00    20.451124
2020-07-01 00:30:00    45.018614
2020-07-01 00:45:00    42.100933
2020-07-01 01:00:00    54.247559
                         ...    
2020-09-12 13:00:00    53.593651
2020-09-12 13:15:00    46.486775
2020-09-12 13:30:00    25.772109
2020-09-12 13:45:00    35.940168
2020-09-12 14:00:00    21.367652
Freq: 15T, Name: predicted_mean, Length: 7065, dtype: float64
3.9341719584649053
-32.11253903409945
2020-07-01 00:00:00     3.934172
2020-07-01 00:15:00    20.451124
2020-07

...

2020-07-01 00:00:00     0.000000
2020-07-01 00:15:00    20.713192
2020-07-01 00:30:00    45.605835
2020-07-01 00:45:00    42.563636
2020-07-01 01:00:00    55.013886
                         ...    
2020-09-12 13:00:00    54.278687
2020-09-12 13:15:00    46.772680
2020-09-12 13:30:00    25.942356
2020-09-12 13:45:00    36.202869
2020-09-12 14:00:00    21.582307
Freq: 15T, Name: predicted_mean, Length: 7065, dtype: float64
0.0
42.42666680929365
2020-07-01 00:00:00     0.000000
2020-07-01 00:15:00    20.713192
2020-07-01 00:30:00    45.605835
2020-07-01 00:45:00    42.563636
2020-07-01 01:00:00    55.013886
                         ...    
2020-09-12 13:00:00    54.278687
2020-09-12 13:15:00    46.772680
2020-09-12 13:30:00    25.942356
2020-09-12 13:45:00    36.202869
2020-09-12 14:00:00    21.582307
Freq: 15T, Name: predicted_mean, Length: 7065, dtype: float64
0.0
42.72521805271671
2020-07-01 00:00:00     0.000000
2020-07-01 00:15:00    20.713192
2020-07-01 00:30:00    45.605835
2020-07

2020-07-01 00:00:00     0.000000
2020-07-01 00:15:00    20.713192
2020-07-01 00:30:00    45.605835
2020-07-01 00:45:00    42.563636
2020-07-01 01:00:00    55.013886
                         ...    
2020-09-12 13:00:00    54.278687
2020-09-12 13:15:00    46.772680
2020-09-12 13:30:00    25.942356
2020-09-12 13:45:00    36.202869
2020-09-12 14:00:00    21.582307
Freq: 15T, Name: predicted_mean, Length: 7065, dtype: float64
0.0
-17.38891547104814
2020-07-01 00:00:00     0.000000
2020-07-01 00:15:00    20.713192
2020-07-01 00:30:00    45.605835
2020-07-01 00:45:00    42.563636
2020-07-01 01:00:00    55.013886
                         ...    
2020-09-12 13:00:00    54.278687
2020-09-12 13:15:00    46.772680
2020-09-12 13:30:00    25.942356
2020-09-12 13:45:00    36.202869
2020-09-12 14:00:00    21.582307
Freq: 15T, Name: predicted_mean, Length: 7065, dtype: float64
0.0
-17.35703089429172
2020-07-01 00:00:00     0.000000
2020-07-01 00:15:00    20.713192
2020-07-01 00:30:00    45.605835
2020-

2020-07-01 00:00:00     0.000000
2020-07-01 00:15:00    20.713192
2020-07-01 00:30:00    45.605835
2020-07-01 00:45:00    42.563636
2020-07-01 01:00:00    55.013886
                         ...    
2020-09-12 13:00:00    54.278687
2020-09-12 13:15:00    46.772680
2020-09-12 13:30:00    25.942356
2020-09-12 13:45:00    36.202869
2020-09-12 14:00:00    21.582307
Freq: 15T, Name: predicted_mean, Length: 7065, dtype: float64
0.0
-21.348055638451747
2020-07-01 00:00:00     0.000000
2020-07-01 00:15:00    20.713192
2020-07-01 00:30:00    45.605835
2020-07-01 00:45:00    42.563636
2020-07-01 01:00:00    55.013886
                         ...    
2020-09-12 13:00:00    54.278687
2020-09-12 13:15:00    46.772680
2020-09-12 13:30:00    25.942356
2020-09-12 13:45:00    36.202869
2020-09-12 14:00:00    21.582307
Freq: 15T, Name: predicted_mean, Length: 7065, dtype: float64
0.0
-20.94943863147203
2020-07-01 00:00:00     0.000000
2020-07-01 00:15:00    20.713192
2020-07-01 00:30:00    45.605835
2020

2020-07-01 00:00:00     0.000000
2020-07-01 00:15:00    20.713192
2020-07-01 00:30:00    45.605835
2020-07-01 00:45:00    42.563636
2020-07-01 01:00:00    55.013886
                         ...    
2020-09-12 13:00:00    54.278687
2020-09-12 13:15:00    46.772680
2020-09-12 13:30:00    25.942356
2020-09-12 13:45:00    36.202869
2020-09-12 14:00:00    21.582307
Freq: 15T, Name: predicted_mean, Length: 7065, dtype: float64
0.0
-24.501734172650828
2020-07-01 00:00:00     0.000000
2020-07-01 00:15:00    20.713192
2020-07-01 00:30:00    45.605835
2020-07-01 00:45:00    42.563636
2020-07-01 01:00:00    55.013886
                         ...    
2020-09-12 13:00:00    54.278687
2020-09-12 13:15:00    46.772680
2020-09-12 13:30:00    25.942356
2020-09-12 13:45:00    36.202869
2020-09-12 14:00:00    21.582307
Freq: 15T, Name: predicted_mean, Length: 7065, dtype: float64
0.0
-24.46978383233777
2020-07-01 00:00:00     0.000000
2020-07-01 00:15:00    20.713192
2020-07-01 00:30:00    45.605835
2020

2020-07-01 00:00:00     0.000000
2020-07-01 00:15:00    20.713192
2020-07-01 00:30:00    45.605835
2020-07-01 00:45:00    42.563636
2020-07-01 01:00:00    55.013886
                         ...    
2020-09-12 13:00:00    54.278687
2020-09-12 13:15:00    46.772680
2020-09-12 13:30:00    25.942356
2020-09-12 13:45:00    36.202869
2020-09-12 14:00:00    21.582307
Freq: 15T, Name: predicted_mean, Length: 7065, dtype: float64
0.0
-25.10599459555788
2020-07-01 00:00:00     0.000000
2020-07-01 00:15:00    20.713192
2020-07-01 00:30:00    45.605835
2020-07-01 00:45:00    42.563636
2020-07-01 01:00:00    55.013886
                         ...    
2020-09-12 13:00:00    54.278687
2020-09-12 13:15:00    46.772680
2020-09-12 13:30:00    25.942356
2020-09-12 13:45:00    36.202869
2020-09-12 14:00:00    21.582307
Freq: 15T, Name: predicted_mean, Length: 7065, dtype: float64
0.0
-24.974044255244827
2020-07-01 00:00:00     0.000000
2020-07-01 00:15:00    20.713192
2020-07-01 00:30:00    45.605835
2020

In [37]:
mse7, mse8 = runModels(df4, (3,1,1))

C:\Users\bvits\anaconda3\envs\modern_ts\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: No frequency information was provided, so inferred frequency 15T will be used.
  self._init_dates(dates, freq)
C:\Users\bvits\anaconda3\envs\modern_ts\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: No frequency information was provided, so inferred frequency 15T will be used.
  self._init_dates(dates, freq)
C:\Users\bvits\anaconda3\envs\modern_ts\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: No frequency information was provided, so inferred frequency 15T will be used.
  self._init_dates(dates, freq)
C:\Users\bvits\anaconda3\envs\modern_ts\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: No frequency information was provided, so inferred frequency 15T will be used.
  self._init_dates(dates, freq)
C:\Users\bvits\anaconda3\envs\modern_ts\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: N

2020-10-01 00:00:00     0.000000
2020-10-01 00:15:00   -29.158081
2020-10-01 00:30:00   -29.353922
2020-10-01 00:45:00   -30.172069
2020-10-01 01:00:00   -29.151671
                         ...    
2020-12-13 13:00:00   -26.974447
2020-12-13 13:15:00   -26.685525
2020-12-13 13:30:00   -17.652306
2020-12-13 13:45:00   -18.067036
2020-12-13 14:00:00    -3.667032
Freq: 15T, Name: predicted_mean, Length: 7065, dtype: float64
0.0
71.39918819741972
2020-10-01 00:00:00     0.000000
2020-10-01 00:15:00   -29.158081
2020-10-01 00:30:00   -29.353922
2020-10-01 00:45:00   -30.172069
2020-10-01 01:00:00   -29.151671
                         ...    
2020-12-13 13:00:00   -26.974447
2020-12-13 13:15:00   -26.685525
2020-12-13 13:30:00   -17.652306
2020-12-13 13:45:00   -18.067036
2020-12-13 14:00:00    -3.667032
Freq: 15T, Name: predicted_mean, Length: 7065, dtype: float64
0.0
100.06439463442396
2020-10-01 00:00:00     0.000000
2020-10-01 00:15:00   -29.158081
2020-10-01 00:30:00   -29.353922
2020-1

2020-10-01 00:00:00     0.000000
2020-10-01 00:15:00   -29.158081
2020-10-01 00:30:00   -29.353922
2020-10-01 00:45:00   -30.172069
2020-10-01 01:00:00   -29.151671
                         ...    
2020-12-13 13:00:00   -26.974447
2020-12-13 13:15:00   -26.685525
2020-12-13 13:30:00   -17.652306
2020-12-13 13:45:00   -18.067036
2020-12-13 14:00:00    -3.667032
Freq: 15T, Name: predicted_mean, Length: 7065, dtype: float64
0.0
92.93815236983424
2020-10-01 00:00:00     0.000000
2020-10-01 00:15:00   -29.158081
2020-10-01 00:30:00   -29.353922
2020-10-01 00:45:00   -30.172069
2020-10-01 01:00:00   -29.151671
                         ...    
2020-12-13 13:00:00   -26.974447
2020-12-13 13:15:00   -26.685525
2020-12-13 13:30:00   -17.652306
2020-12-13 13:45:00   -18.067036
2020-12-13 14:00:00    -3.667032
Freq: 15T, Name: predicted_mean, Length: 7065, dtype: float64
0.0
90.1700254735051
2020-10-01 00:00:00     0.000000
2020-10-01 00:15:00   -29.158081
2020-10-01 00:30:00   -29.353922
2020-10-

2020-10-01 00:00:00     0.000000
2020-10-01 00:15:00   -29.158081
2020-10-01 00:30:00   -29.353922
2020-10-01 00:45:00   -30.172069
2020-10-01 01:00:00   -29.151671
                         ...    
2020-12-13 13:00:00   -26.974447
2020-12-13 13:15:00   -26.685525
2020-12-13 13:30:00   -17.652306
2020-12-13 13:45:00   -18.067036
2020-12-13 14:00:00    -3.667032
Freq: 15T, Name: predicted_mean, Length: 7065, dtype: float64
0.0
109.04392288698196
2020-10-01 00:00:00     0.000000
2020-10-01 00:15:00   -29.158081
2020-10-01 00:30:00   -29.353922
2020-10-01 00:45:00   -30.172069
2020-10-01 01:00:00   -29.151671
                         ...    
2020-12-13 13:00:00   -26.974447
2020-12-13 13:15:00   -26.685525
2020-12-13 13:30:00   -17.652306
2020-12-13 13:45:00   -18.067036
2020-12-13 14:00:00    -3.667032
Freq: 15T, Name: predicted_mean, Length: 7065, dtype: float64
0.0
110.17579599065286
2020-10-01 00:00:00     0.000000
2020-10-01 00:15:00   -29.158081
2020-10-01 00:30:00   -29.353922
2020-

2020-10-01 00:00:00     0.000000
2020-10-01 00:15:00   -29.158081
2020-10-01 00:30:00   -29.353922
2020-10-01 00:45:00   -30.172069
2020-10-01 01:00:00   -29.151671
                         ...    
2020-12-13 13:00:00   -26.974447
2020-12-13 13:15:00   -26.685525
2020-12-13 13:30:00   -17.652306
2020-12-13 13:45:00   -18.067036
2020-12-13 14:00:00    -3.667032
Freq: 15T, Name: predicted_mean, Length: 7065, dtype: float64
0.0
100.0601673124851
2020-10-01 00:00:00     0.000000
2020-10-01 00:15:00   -29.158081
2020-10-01 00:30:00   -29.353922
2020-10-01 00:45:00   -30.172069
2020-10-01 01:00:00   -29.151671
                         ...    
2020-12-13 13:00:00   -26.974447
2020-12-13 13:15:00   -26.685525
2020-12-13 13:30:00   -17.652306
2020-12-13 13:45:00   -18.067036
2020-12-13 14:00:00    -3.667032
Freq: 15T, Name: predicted_mean, Length: 7065, dtype: float64
0.0
100.25870708282264
2020-10-01 00:00:00     0.000000
2020-10-01 00:15:00   -29.158081
2020-10-01 00:30:00   -29.353922
2020-1

...

2020-10-01 00:00:00     0.000000
2020-10-01 00:15:00   -29.158081
2020-10-01 00:30:00   -29.353945
2020-10-01 00:45:00   -30.172299
2020-10-01 01:00:00   -29.152830
                         ...    
2020-12-13 13:00:00   -26.663788
2020-12-13 13:15:00   -26.669588
2020-12-13 13:30:00   -17.529018
2020-12-13 13:45:00   -17.916158
2020-12-13 14:00:00    -3.558606
Freq: 15T, Name: predicted_mean, Length: 7065, dtype: float64
0.0
-29.20914072692416
2020-10-01 00:00:00     0.000000
2020-10-01 00:15:00   -29.158081
2020-10-01 00:30:00   -29.353945
2020-10-01 00:45:00   -30.172299
2020-10-01 01:00:00   -29.152830
                         ...    
2020-12-13 13:00:00   -26.663788
2020-12-13 13:15:00   -26.669588
2020-12-13 13:30:00   -17.529018
2020-12-13 13:45:00   -17.916158
2020-12-13 14:00:00    -3.558606
Freq: 15T, Name: predicted_mean, Length: 7065, dtype: float64
0.0
-28.777220449203835
2020-10-01 00:00:00     0.000000
2020-10-01 00:15:00   -29.158081
2020-10-01 00:30:00   -29.353945
2020

2020-10-01 00:00:00     0.000000
2020-10-01 00:15:00   -29.158081
2020-10-01 00:30:00   -29.353945
2020-10-01 00:45:00   -30.172299
2020-10-01 01:00:00   -29.152830
                         ...    
2020-12-13 13:00:00   -26.663788
2020-12-13 13:15:00   -26.669588
2020-12-13 13:30:00   -17.529018
2020-12-13 13:45:00   -17.916158
2020-12-13 14:00:00    -3.558606
Freq: 15T, Name: predicted_mean, Length: 7065, dtype: float64
0.0
82.17609001766449
2020-10-01 00:00:00     0.000000
2020-10-01 00:15:00   -29.158081
2020-10-01 00:30:00   -29.353945
2020-10-01 00:45:00   -30.172299
2020-10-01 01:00:00   -29.152830
                         ...    
2020-12-13 13:00:00   -26.663788
2020-12-13 13:15:00   -26.669588
2020-12-13 13:30:00   -17.529018
2020-12-13 13:45:00   -17.916158
2020-12-13 14:00:00    -3.558606
Freq: 15T, Name: predicted_mean, Length: 7065, dtype: float64
0.0
79.8746769620515
2020-10-01 00:00:00     0.000000
2020-10-01 00:15:00   -29.158081
2020-10-01 00:30:00   -29.353945
2020-10-

2020-10-01 00:00:00     0.000000
2020-10-01 00:15:00   -29.158081
2020-10-01 00:30:00   -29.353945
2020-10-01 00:45:00   -30.172299
2020-10-01 01:00:00   -29.152830
                         ...    
2020-12-13 13:00:00   -26.663788
2020-12-13 13:15:00   -26.669588
2020-12-13 13:30:00   -17.529018
2020-12-13 13:45:00   -17.916158
2020-12-13 14:00:00    -3.558606
Freq: 15T, Name: predicted_mean, Length: 7065, dtype: float64
0.0
-36.457360770724094
2020-10-01 00:00:00     0.000000
2020-10-01 00:15:00   -29.158081
2020-10-01 00:30:00   -29.353945
2020-10-01 00:45:00   -30.172299
2020-10-01 01:00:00   -29.152830
                         ...    
2020-12-13 13:00:00   -26.663788
2020-12-13 13:15:00   -26.669588
2020-12-13 13:30:00   -17.529018
2020-12-13 13:45:00   -17.916158
2020-12-13 14:00:00    -3.558606
Freq: 15T, Name: predicted_mean, Length: 7065, dtype: float64
0.0
-36.19208968055776
2020-10-01 00:00:00     0.000000
2020-10-01 00:15:00   -29.158081
2020-10-01 00:30:00   -29.353945
2020

2020-10-01 00:00:00     0.000000
2020-10-01 00:15:00   -29.158081
2020-10-01 00:30:00   -29.353945
2020-10-01 00:45:00   -30.172299
2020-10-01 01:00:00   -29.152830
                         ...    
2020-12-13 13:00:00   -26.663788
2020-12-13 13:15:00   -26.669588
2020-12-13 13:30:00   -17.529018
2020-12-13 13:45:00   -17.916158
2020-12-13 14:00:00    -3.558606
Freq: 15T, Name: predicted_mean, Length: 7065, dtype: float64
0.0
-0.9215754206619158
2020-10-01 00:00:00     0.000000
2020-10-01 00:15:00   -29.158081
2020-10-01 00:30:00   -29.353945
2020-10-01 00:45:00   -30.172299
2020-10-01 01:00:00   -29.152830
                         ...    
2020-12-13 13:00:00   -26.663788
2020-12-13 13:15:00   -26.669588
2020-12-13 13:30:00   -17.529018
2020-12-13 13:45:00   -17.916158
2020-12-13 14:00:00    -3.558606
Freq: 15T, Name: predicted_mean, Length: 7065, dtype: float64
0.0
-0.2563043304955732
2020-10-01 00:00:00     0.000000
2020-10-01 00:15:00   -29.158081
2020-10-01 00:30:00   -29.353945
202

2020-10-01 00:00:00     0.000000
2020-10-01 00:15:00   -29.158081
2020-10-01 00:30:00   -29.353945
2020-10-01 00:45:00   -30.172299
2020-10-01 01:00:00   -29.152830
                         ...    
2020-12-13 13:00:00   -26.663788
2020-12-13 13:15:00   -26.669588
2020-12-13 13:30:00   -17.529018
2020-12-13 13:45:00   -17.916158
2020-12-13 14:00:00    -3.558606
Freq: 15T, Name: predicted_mean, Length: 7065, dtype: float64
0.0
-32.319410033987175
2020-10-01 00:00:00     0.000000
2020-10-01 00:15:00   -29.158081
2020-10-01 00:30:00   -29.353945
2020-10-01 00:45:00   -30.172299
2020-10-01 01:00:00   -29.152830
                         ...    
2020-12-13 13:00:00   -26.663788
2020-12-13 13:15:00   -26.669588
2020-12-13 13:30:00   -17.529018
2020-12-13 13:45:00   -17.916158
2020-12-13 14:00:00    -3.558606
Freq: 15T, Name: predicted_mean, Length: 7065, dtype: float64
0.0
-32.1541294469605
2020-10-01 00:00:00     0.000000
2020-10-01 00:15:00   -29.158081
2020-10-01 00:30:00   -29.353945
2020-

In [38]:
d = {'Season 1':mse1,'Season 2':mse3,'Season 3':mse5,'Season 4':mse7}
df_errors_autoArima = pd.DataFrame({k:pd.Series(v) for k,v in d.items()})
d = {'Season 1':mse2,'Season 2':mse4,'Season 3':mse6,'Season 4':mse8}
df_errors_acfArima = pd.DataFrame({k:pd.Series(v) for k,v in d.items()})

df_errors_autoArima.to_csv('autoARIMA_errors_final.csv')

df_errors_acfArima.to_csv('acfARIMA_errors_final.csv')